# Notebook per la conversione del datasample SWARM_TEC

In questo notebook facciamo uso delle librerie python 

pandas & astropy

per leggere una tabella in formato txt, importarla come un dataframe e salvarlo in csv, trasformare il dataframe in una Qtable di astropy e trasformare la Qtable in VOTable, salvare la VOTable in formato xml.


In [47]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

#from astropy.table import Table
from astropy.table import QTable
import astropy.units as u
import astropy.coordinates as astrocoord

from astropy.io import votable 
from astropy.io.votable import from_table, writeto, parse

Dopo aver importato tutte le librerie necessarie, leggiamo il file txt e creiamo la colonna standard del tempo.

In [48]:
directory='./'
file1='Swarm_TEC_A_2014_01_PRN=01_ROTI10s.txt'

df1 = pd.read_csv(directory+file1, sep='\s+', header=0)    #lettura del file txt. Indica esplicitamente che l'header è alla row 0

datestring=[]             # loop per usare le prime colonne per costruire il formato di tempo 'standard'
i=0
for datet in zip(df1["year"],df1["month"],df1["day"],df1["hour"],df1["min"],df1["sec"],df1["msec"]):
    datestring.append("%4i-%2.2i-%2.2iT%2.2i:%2.2i:%2.2i.%4.4i" %(datet))
    #print(datestring[i])
    i+=1

df1.insert(0, 'Time', datestring) # inserire la colonna Time come prima colonna
df1.rename(columns={"Radius(m)": "Radius", "Height(km)": "Height"},inplace=True)  #rinominare le colonne per leiminare le units nel nome
df1.rename(columns={"sTEC(TECU)": "sTEC", "ROT(TECU/s)": "ROT"},inplace=True)
df1.rename(columns={"ROTI_10s(TECU/s)": "ROTI_10s", "ROT_mean_10s(TECU/s)": "ROT_mean_10s"},inplace=True)
df1.rename(columns={"mean_sTEC(TECU)": "mean_sTEC"},inplace=True)


LON=[]
LAT=[]
DIST=[]
for PHI,THETA,Z in zip(df1["LatGeo"],df1["LonGeo"],df1["Radius"]):   
    LON.append(THETA)
    LAT.append(PHI)
    DIST.append(Z)


df1.insert(1, 'GEI_lon', LON) # inserire la colonna LON
df1.insert(2, 'GEI_lat', LAT) # inserire la colonna LAT
df1.insert(3, 'GEI_distance', DIST) # inserire la colonna LAT

#df1.to_csv(directory+file_out, index=False)

Adesso creiamo le righe con la tipologia di dataentry e le units per ogni colonna.
Piccolo trucco per inserirle alla fine, e poi shiftare l'indice per avere gli header nelle prime tre righe 

In [49]:
head1=df1.columns   
head_type=["datetime","float","float","float","int","int","int","int","int","int","int","int","float","float","float","float","float","float","float","float","float","float","float","float","float","float","float","float"]
head_quantity=["UTC","deg","deg","m"," "," "," "," "," "," "," "," "," "," "," ","deg","deg","m","km","deg","deg","deg"," ","TECU","TECU/s","TECU/s","TECU/s","TECU"]

null_type=["-",np.nan,np.nan,np.nan,"-9999","-","-","-",-9999,-9999,np.nan,np.nan,'-',-9999,-9999,-9999,'-',np.nan,np.nan,np.nan,np.nan,np.nan,np.nan,np.nan,-9999,'-',-9999,-9999,np.nan,np.nan,np.nan,np.nan,'-']


df1.loc[-1] = head3  # adding the headers at the end 
df1.loc[-2] = head2  # adding 
df1.loc[-3] = head1  # adding 


df1.loc[-1] = head_quantity  # adding the headers at the end 
df1.loc[-2] = null_type  # adding 
df1.loc[-3] = head_type  # adding 

df1.drop([0],inplace=True)
df1.index=df1.index +3
df = df1.sort_index()
df

Time    GEI_lon   GEI_lat  GEI_distance  year  month  \
0                        Time    GEI_lon   GEI_lat  GEI_distance  year  month   
1                    datetime      float     float         float   int    int   
2                         UTC        deg       deg             m                
4    2014-01-01T00:47:34.0000  153.98361   2.06938    6873901.73  2014      1   
5    2014-01-01T00:47:44.0000  153.96892   2.70379    6873825.25  2014      1   
..                        ...        ...       ...           ...   ...    ...   
97   2014-01-01T03:25:44.0000  -60.72707 -64.16177     6880536.5  2014      1   
98   2014-01-01T03:25:54.0000  -60.62331 -64.79169     6880522.7  2014      1   
99   2014-01-01T03:26:04.0000  -60.51259 -65.42146    6880508.53  2014      1   
100  2014-01-01T03:26:14.0000  -60.39436 -66.05106    6880494.02  2014      1   
101  2014-01-01T03:26:24.0000  -60.26801 -66.68049    6880479.16  2014      1   

     day  hour  min  sec  ...  Height  LatMagQD   LonMagQD  Elevation_Angle  \
0    day  hour  min  sec  ...  Height  LatMagQD   LonMagQD  Elevation_Angle   
1    int   int  int  int  ...   float     float      float            float   
2                         ...      km       deg        deg              deg   
4      1     0   47   34  ...  502.89   -5.0636 -133.48372            20.03   
5      1     0   47   44  ...  502.82  -4.41792 -133.55859            20.18   
..   ...   ...  ...  ...  ...     ...       ...        ...              ...   
97     1     3   25   44  ...  509.53 -50.45309     10.969            36.78   
98     1     3   25   54  ...  509.52 -51.03748   11.14034            36.94   
99     1     3   26    4  ...   509.5 -51.62206   11.31611            37.09   
100    1     3   26   14  ...  509.49 -52.20681   11.49645            37.23   
101    1     3   26   24  ...  509.47 -52.79174   11.68147            37.36   

        Abs     sTEC      ROT  ROTI_10s  ROT_mean_10s  mean_sTEC  
0       Abs     sTEC      ROT  ROTI_10s  ROT_mean_10s  mean_sTEC  
1     float    float    float     float         float      float  
2               TECU   TECU/s    TECU/s        TECU/s       TECU  
4    47.773 -0.02367      NaN       NaN           NaN        NaN  
5    47.537 -0.02126      NaN       NaN           NaN        NaN  
..      ...      ...      ...       ...           ...        ...  
97   23.081 -0.00234  0.00964  -0.00101        23.175        NaN  
98   23.057   0.0155  0.00899   0.00007        23.165        NaN  
99   23.212 -0.00706  0.00926   -0.0004        23.165        NaN  
100  23.142  0.00149  0.00801  -0.00256        23.161        NaN  
101  23.157  0.00245  0.00783  -0.00199        23.136        NaN  

[101 rows x 28 columns]

Definizione nome output e
Scrittura del file in formato csv

In [45]:
file_out='Swarm_TEC_A_2014_01_PRN=01_ROTI10s.csv'
df.to_csv(directory+file_out, index=False)

Per verificare che la scrittura sia andata a buon fine, re-importiamo il dataframe

In [46]:
df_check = pd.read_csv(directory+file_out)
df_check

Time    GEI_lon    GEI_lat  GEI_distance  year  \
0                        Time    GEI_lon    GEI_lat  GEI_distance  year   
1                    datetime      float      float         float   int   
2                         UTC        deg        deg             m         
3    2014-01-01T00:47:34.0000  153.98361    2.06938    6873901.73  2014   
4    2014-01-01T00:47:44.0000  153.96892    2.70379    6873825.25  2014   
..                        ...        ...        ...           ...   ...   
96   2014-01-01T03:25:44.0000  -60.72707  -64.16177     6880536.5  2014   
97   2014-01-01T03:25:54.0000  -60.62331  -64.79169     6880522.7  2014   
98   2014-01-01T03:26:04.0000  -60.51259  -65.42146    6880508.53  2014   
99   2014-01-01T03:26:14.0000  -60.39436  -66.05106    6880494.02  2014   
100  2014-01-01T03:26:24.0000  -60.26801  -66.68049    6880479.16  2014   

     month  day  hour  min  sec  ...  Height   LatMagQD    LonMagQD  \
0    month  day  hour  min  sec  ...  Height   LatMagQD    LonMagQD   
1      int  int   int  int  int  ...   float      float       float   
2                                ...      km        deg         deg   
3        1    1     0   47   34  ...  502.89    -5.0636  -133.48372   
4        1    1     0   47   44  ...  502.82   -4.41792  -133.55859   
..     ...  ...   ...  ...  ...  ...     ...        ...         ...   
96       1    1     3   25   44  ...  509.53  -50.45309      10.969   
97       1    1     3   25   54  ...  509.52  -51.03748    11.14034   
98       1    1     3   26    4  ...   509.5  -51.62206    11.31611   
99       1    1     3   26   14  ...  509.49  -52.20681    11.49645   
100      1    1     3   26   24  ...  509.47  -52.79174    11.68147   

     Elevation_Angle     Abs      sTEC      ROT  ROTI_10s  ROT_mean_10s  \
0    Elevation_Angle     Abs      sTEC      ROT  ROTI_10s  ROT_mean_10s   
1              float   float     float    float     float         float   
2                deg              TECU   TECU/s    TECU/s        TECU/s   
3              20.03  47.773  -0.02367      NaN       NaN           NaN   
4              20.18  47.537  -0.02126      NaN       NaN           NaN   
..               ...     ...       ...      ...       ...           ...   
96             36.78  23.081  -0.00234  0.00964  -0.00101        23.175   
97             36.94  23.057    0.0155  0.00899     7e-05        23.165   
98             37.09  23.212  -0.00706  0.00926   -0.0004        23.165   
99             37.23  23.142   0.00149  0.00801  -0.00256        23.161   
100            37.36  23.157   0.00245  0.00783  -0.00199        23.136   

     mean_sTEC  
0    mean_sTEC  
1        float  
2         TECU  
3          NaN  
4          NaN  
..         ...  
96         NaN  
97         NaN  
98         NaN  
99         NaN  
100        NaN  

[101 rows x 28 columns]

Prepariamo i dati per l'inserimento in una Qtable di astropy.

Forziamo il type sulle colonne (adesso sono tutte delle stringhe)


In [6]:
df_new=df_check.drop([0,1])
df_new['year'] = df_new['year'].astype(int)
df_new['month'] = df_new['month'].astype(int)
df_new['day'] = df_new['day'].astype(int)
df_new['hour'] = df_new['hour'].astype(int)
df_new['min'] = df_new['min'].astype(int)
df_new['sec'] = df_new['sec'].astype(int)
df_new['msec'] = df_new['msec'].astype(int)
df_new['doy'] = df_new['doy'].astype(int)

df_new['hourUT'] = df_new['hourUT'].astype(float)
df_new['hourLT'] = df_new['hourLT'].astype(float)
df_new['MLT'] = df_new['MLT'].astype(float)
df_new['LatGeo'] = df_new['LatGeo'].astype(float)
df_new['LonGeo'] = df_new['LonGeo'].astype(float)
df_new['Radius'] = df_new['Radius'].astype(float)
df_new['Height'] = df_new['Height'].astype(float)

df_new['LatMagQD'] = df_new['LatMagQD'].astype(float)
df_new['LonMagQD'] = df_new['LonMagQD'].astype(float)
df_new['Elevation_Angle'] = df_new['Elevation_Angle'].astype(float)
df_new['Abs'] = df_new['Abs'].astype(float)

df_new['sTEC'] = df_new['sTEC'].astype(float)
df_new['ROT'] = df_new['ROT'].astype(float)
df_new['ROTI_10s'] = df_new['ROTI_10s'].astype(float)
df_new['ROT_mean_10s'] = df_new['ROT_mean_10s'].astype(float)
df_new['mean_sTEC'] = df_new['mean_sTEC'].astype(float)

#type(df_new['Height'])


Inseriamo i dati in una Qtable di astropy.

E dopo possiamo associare le units alle colonne.

Extra: definiamo la nuova unit TECU

In [7]:
# https://docs.astropy.org/en/stable/table/pandas.html
ATable= QTable.from_pandas(df_new)

TECU = u.def_unit('TECU', 1e16* u.electron / (u.m ** 2))

ATable['year'] = ATable['year']
ATable['month'] = ATable['month']
ATable['day'] = ATable['day']*u.day
ATable['hour'] = ATable['hour']*u.hour
ATable['min'] = ATable['min']*u.minute
ATable['sec'] = ATable['sec']*u.s
ATable['msec'] = ATable['msec']*u.ms
ATable['doy'] = ATable['doy']*u.day

ATable['hourUT'] = ATable['hourUT']*u.hour
ATable['hourLT'] = ATable['hourLT']*u.hour
ATable['MLT'] = ATable['MLT']*u.hour
ATable['LatGeo'] = ATable['LatGeo']*u.deg
ATable['LonGeo'] = ATable['LonGeo']*u.deg
ATable['Radius'] = ATable['Radius']*u.m
ATable['Height'] = ATable['Height']*u.km

ATable['LatMagQD'] = ATable['LatMagQD']*u.deg
ATable['LonMagQD'] = ATable['LonMagQD']*u.deg
ATable['Elevation_Angle'] = ATable['Elevation_Angle']*u.deg
ATable['Abs'] = ATable['Abs']*u.deg

ATable['sTEC'] = ATable['sTEC']*TECU
ATable['ROT'] = ATable['ROT']*TECU
ATable['ROTI_10s'] = ATable['ROTI_10s']*TECU/u.s
ATable['ROT_mean_10s'] = ATable['ROT_mean_10s']*TECU/u.s
ATable['mean_sTEC'] = ATable['mean_sTEC']*TECU

ATable

<QTable length=98>
          Time            year month ... ROTI_10s ROT_mean_10s mean_sTEC
                                     ... TECU / s   TECU / s      TECU  
         str24           int64 int64 ... float64    float64     float64 
------------------------ ----- ----- ... -------- ------------ ---------
2014-01-01T00:47:34.0000  2014     1 ...      nan          nan       nan
2014-01-01T00:47:44.0000  2014     1 ...      nan          nan       nan
2014-01-01T00:47:54.0000  2014     1 ...      nan          nan       nan
2014-01-01T00:48:04.0000  2014     1 ...      nan          nan       nan
2014-01-01T00:48:14.0000  2014     1 ...      nan          nan       nan
2014-01-01T00:48:24.0000  2014     1 ... -0.02523       46.795       nan
                     ...   ...   ... ...      ...          ...       ...
2014-01-01T03:25:34.0000  2014     1 ... -0.00136       23.189       nan
2014-01-01T03:25:44.0000  2014     1 ... -0.00101       23.175       nan
2014-01-01T03:25:54.0000  2014     1 ...    7e-05       23.165       nan
2014-01-01T03:26:04.0000  2014     1 ...  -0.0004       23.165       nan
2014-01-01T03:26:14.0000  2014     1 ... -0.00256       23.161       nan
2014-01-01T03:26:24.0000  2014     1 ... -0.00199       23.136       nan

Trasformiamo la astropy Qtable in una VOTable e la scriviamo su file

In [8]:
#https://docs.astropy.org/en/stable/io/votable/index.html
votable = from_table(ATable)
file_out2='Swarm_TEC_A_2014_01_PRN=01_ROTI10s.xml'
writeto(votable, file_out2)


Per verificare che la scrittura sia andata a buon fine, re-importiamo la VOTable

In [9]:
votable = parse(file_out2)
intable = votable.get_first_table()
intable.array["Radius"]

masked_array(data=[6873901.73, 6873825.25, 6873748.27, 6873670.8,
                   6873592.84, 6873514.41, 6873435.52, 6873356.19,
                   6873276.42, 6873196.22, 6873115.62, 6873034.63,
                   6872953.26, 6872871.52, 6872789.44, 6872707.02,
                   6872624.28, 6872541.24, 6872457.91, 6872374.31,
                   6872290.45, 6872206.36, 6872122.04, 6872037.52,
                   6871952.81, 6871867.94, 6871782.91, 6871697.75,
                   6871612.47, 6871527.1, 6871441.65, 6871356.15,
                   6871270.6, 6871185.04, 6871099.49, 6871013.95,
                   6870928.47, 6870843.04, 6870757.71, 6870672.48,
                   6870587.38, 6870502.43, 6870417.65, 6870333.06,
                   6880512.53, 6880531.57, 6880549.65, 6880566.79,
                   6880583.0, 6880598.27, 6880612.64, 6880626.1,
                   6880638.66, 6880650.35, 6880661.17, 6880671.13,
                   6880680.24, 6880688.52, 6880695.98, 6880702.62,
